### Load dependencies

In [1]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'  

from netCDF4 import Dataset, num2date, date2index
from datetime import datetime

import time as tm
import numpy as np
import numpy.ma as ma
from numpy import argmin, linspace, size, array

from cdo import *
cdo = Cdo()

import matplotlib.pyplot as plt
import matplotlib.path as mpath
import matplotlib.colors as colors
import matplotlib.patches as mpatches
from matplotlib.pyplot import cm
from matplotlib.gridspec import GridSpec
from matplotlib.colors import ListedColormap

import cartopy as cp
import cartopy.feature as cfeature
import cartopy.crs as ccrs
from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter
from cartopy.mpl.gridliner import LONGITUDE_FORMATTER, LATITUDE_FORMATTER
import matplotlib.ticker as mticker

from shapely import geometry
from collections import namedtuple
from shapely.geometry.polygon import LinearRing

import seaborn as sns
import xarray as xr
import pandas as pd

In [2]:
#Add regional boxes
Region = namedtuple('Region',field_names=['region_name','lonmin','lonmax','latmin','latmax'])

subpolar  =  Region(region_name="Sub-polar North Atlantic",
                       lonmin=-60,
                       lonmax=-10,
                       latmin=65,
                       latmax=50)

subtropic =  Region(region_name="Sub-tropical North Atlantic",
                       lonmin=-90,
                       lonmax=-10,
                       latmin=40,
                       latmax=15)

In [3]:
from matplotlib.colors import ListedColormap, LinearSegmentedColormap

colors = ['midnightblue','mediumblue','blue','dodgerblue','deepskyblue','lightskyblue','white','yellow','orange','orangered','red','firebrick','purple']
cmap1 = LinearSegmentedColormap.from_list("mycmap", colors)
nodes = [0, 0.1, 0.35,0.4,0.45,0.475,0.5,0.525,0.55,0.60,0.65,0.9, 1.0]
cmap2 = LinearSegmentedColormap.from_list("mycmap", list(zip(nodes, colors)))

### Load data
### Observation-based Ensemble Mean

In [5]:
f1 = xr.open_dataset('../data/ens_1990-2020_co2.nc') # PgC m-2 yr-1
f2 = f1.co2flux.sel(lon=slice(-90,-10),lat=slice(15,65))
f2 = f2.where(((f2.lat<50) + (f2.lon>-60)),drop=True)

In [6]:
# Maps

obs_yr = f2.groupby('time.year').mean(dim='time').mean(dim='year')

seasons_obs = f2.groupby('time.season').mean(dim='time')
obs_DJF = seasons_obs.sel(season='DJF')/4
obs_MAM = seasons_obs.sel(season='MAM')/4
obs_JJA = seasons_obs.sel(season='JJA')/4
obs_SON = seasons_obs.sel(season='SON')/4

In [7]:
observations=['lsce','csir','spco2','jena','jma','nies','ens']

co2_ym=[]
co2_win=[]
co2_spr=[]
co2_sum=[]
co2_aut=[]

lat_o=[]
lon_o=[]

In [8]:
for i in range(0,len(observations)):
    f = '{}{}{}'.format('../data/',observations[i],'_1990-2020_co2.nc')
    f1_1 = cdo.sellonlatbox('-90,-10,15,65', input=f, options='-f nc')
    f1 = cdo.setclonlatbox('0,-89,-60,50,65',input=f1_1, options='-f nc')
    
    #yearmean
    co2_ym_1                      =cdo.yearmean(input=f1, options='-f nc')
    co2_ym_2                      =cdo.fldsum(input=co2_ym_1, options='-f nc')
 
    co2flux_yearmean              =Dataset(co2_ym_2, 'r')
    co2_ym.append(co2flux_yearmean.variables['co2flux'][:,0,0])

    #winter
    co2_win_1                     =cdo.select('season=DJF', input=f1, options='-f nc')
    co2_win_2                     =cdo.yearmean(input=co2_win_1, options='-f nc')
    co2_win_3                     =cdo.fldsum(input=co2_win_2, options='-f nc')

    co2flux_win    =Dataset(co2_win_3, 'r')
    co2_win.append(co2flux_win.variables['co2flux'][:,0,0])
    
    #spring
    co2_spr_1                     =cdo.select('season=MAM', input=f1, options='-f nc')
    co2_spr_2                     =cdo.yearmean(input=co2_spr_1, options='-f nc')
    co2_spr_3                     =cdo.fldsum(input=co2_spr_2, options='-f nc')

    co2flux_spr    =Dataset(co2_spr_3, 'r')
    co2_spr.append(co2flux_spr.variables['co2flux'][:,0,0])

    #summer
    co2_sum_1                     =cdo.select('season=JJA', input=f1, options='-f nc')
    co2_sum_2                     =cdo.yearmean(input=co2_sum_1, options='-f nc')
    co2_sum_3                     =cdo.fldsum(input=co2_sum_2, options='-f nc')

    co2flux_sum    =Dataset(co2_sum_3, 'r')
    co2_sum.append(co2flux_sum.variables['co2flux'][:,0,0])

    #winter
    co2_aut_1                     =cdo.select('season=SON', input=f1, options='-f nc')
    co2_aut_2                     =cdo.yearmean(input=co2_aut_1, options='-f nc')
    co2_aut_3                     =cdo.fldsum(input=co2_aut_2, options='-f nc')

    co2flux_aut    =Dataset(co2_aut_3, 'r')
    co2_aut.append(co2flux_aut.variables['co2flux'][:,0,0])
    
    lon_o.append(co2flux_aut.variables['lon'])
    lat_o.append(co2flux_aut.variables['lat'])

### MPI-GE Ensemble Mean

In [9]:
f3 = xr.open_dataset('../data/mpi_1990-2020_co2.nc')
f4 = f3.sel(depth=0).co2flux.sel(lon=slice(271,350),lat=slice(15,65))
f4 = f4.where(((f3.lat<50) + (f3.lon>300)),drop=True)

In [10]:
#Mean Fluxes

mod_yr = f4.groupby('time.year').mean(dim='time').mean(dim='year')

seasons_mod = f4.groupby('time.season').mean(dim='time')
mod_DJF = seasons_mod.sel(season='DJF')/4
mod_MAM = seasons_mod.sel(season='MAM')/4
mod_JJA = seasons_mod.sel(season='JJA')/4
mod_SON = seasons_mod.sel(season='SON')/4

In [11]:
f2 ='../data/mpi_1990-2020_co2.nc'
f2_1a = cdo.sellonlatbox('-90,-10,15,65', input=f2, options='-f nc')
f2_1 = cdo.setclonlatbox('0,-89,-60,50,65',input=f2_1a, options='-f nc')

mpiesm         = Dataset(f2_1, 'r')
mpige_co2                = mpiesm.variables['co2flux'][:,0,:,:]
print(mpige_co2.shape)
mpige_time               = mpiesm.variables['time']
mpige_lat                = mpiesm.variables['lat']
mpige_lon                = mpiesm.variables['lon']

(360, 50, 81)


In [12]:
#yearmean
co2_ym_1                      =cdo.yearmean(input=f2_1, options='-f nc')
co2_ym_2                      =cdo.fldsum(input=co2_ym_1, options='-f nc')
 
co2flux_yearmean              =Dataset(co2_ym_2, 'r')
co2_ym.append(co2flux_yearmean.variables['co2flux'][:,0,0,0])
    
#winter
co2_win_1                     =cdo.select('season=DJF', input=f2_1, options='-f nc')
co2_win_2                     =cdo.yearmean(input=co2_win_1, options='-f nc')
co2_win_3                     =cdo.fldsum(input=co2_win_2, options='-f nc')

co2flux_win    =Dataset(co2_win_3, 'r')
co2_win.append(co2flux_win.variables['co2flux'][:,0,0,0])
    
#spring
co2_spr_1                     =cdo.select('season=MAM', input=f2_1, options='-f nc')
co2_spr_2                     =cdo.yearmean(input=co2_spr_1, options='-f nc')
co2_spr_3                     =cdo.fldsum(input=co2_spr_2, options='-f nc')

co2flux_spr    =Dataset(co2_spr_3, 'r')
co2_spr.append(co2flux_spr.variables['co2flux'][:,0,0,0])

#summer
co2_sum_1                     =cdo.select('season=JJA', input=f2_1, options='-f nc')
co2_sum_2                     =cdo.yearmean(input=co2_sum_1, options='-f nc')
co2_sum_3                     =cdo.fldsum(input=co2_sum_2, options='-f nc')

co2flux_sum    =Dataset(co2_sum_3, 'r')
co2_sum.append(co2flux_sum.variables['co2flux'][:,0,0,0])
    
#winter
co2_aut_1                     =cdo.select('season=SON', input=f2_1, options='-f nc')
co2_aut_2                     =cdo.yearmean(input=co2_aut_1, options='-f nc')
co2_aut_3                     =cdo.fldsum(input=co2_aut_2, options='-f nc')

co2flux_aut    =Dataset(co2_aut_3, 'r')
co2_aut.append(co2flux_aut.variables['co2flux'][:,0,0,0])
    
lon_o.append(co2flux_aut.variables['lon'])
lat_o.append(co2flux_aut.variables['lat'])

### Figures

In [13]:
#titles = ['Annual Mean','Winter Mean','Spring Mean','Summer Mean','Autumn Mean']
labels1=['a','b','c','d','e']
labels2=['f','g','h','i','j']
data1 = [obs_yr,obs_DJF,obs_MAM,obs_JJA,obs_SON]
data2 = [mod_yr,mod_DJF,mod_MAM,mod_JJA,mod_SON]
lists=[subpolar, subtropic]
subp = geometry.box(minx=subpolar.lonmin,maxx=subpolar.lonmax,miny=subpolar.latmin,maxy=subpolar.latmax)
subt = geometry.box(minx=subtropic.lonmin,maxx=subtropic.lonmax,miny=subtropic.latmin,maxy=subtropic.latmax)

fig, axs = plt.subplots(2, 5, figsize=(18,6), sharex=True, sharey=True, dpi=600)

for i in range(0,5):
    ax          =plt.subplot(2,5,i+1, projection=ccrs.Robinson())
    
    #ax.set_title(titles[i], fontsize=10)
    ax.set_title(labels1[i], fontsize=10, loc='left', fontweight='semibold')
    
    p = plt.contourf(data1[i].lon[:], data1[i].lat[:], data1[i][:,:],
                 levels = np.linspace(-3e-4,3e-4,51),
                 transform      = ccrs.PlateCarree(),
                 cmap           = LinearSegmentedColormap.from_list("mycmap", list(zip(nodes, colors))), extend='both')
    ax.set_extent([270,350,15,65],crs=ccrs.PlateCarree())
    ax.add_geometries([subp], crs=ccrs.PlateCarree(),facecolor='none',edgecolor='black', alpha=0.8, linewidth=0.75)
    ax.add_geometries([subt], crs=ccrs.PlateCarree(),facecolor='none',edgecolor='black', alpha=0.8, linewidth=0.75)

    ax.add_feature(cfeature.GSHHSFeature(edgecolor='k',zorder=1,facecolor='lightgrey',linewidth=0.5))
    
for i in range(0,5):
    ax          =plt.subplot(2,5,i+6, projection=ccrs.Robinson())
    
    #ax.set_title(titles[i], fontsize=10)
    ax.set_title(labels2[i], fontsize=10, loc='left', fontweight='semibold')
    
    plt.contourf(data2[i].lon[:], data2[i].lat[:], data2[i][:,:],
                 levels = np.linspace(-3e-4,3e-4,51),
                 transform      = ccrs.PlateCarree(),
                 cmap           = LinearSegmentedColormap.from_list("mycmap", list(zip(nodes, colors))), extend='both')
    
    ax.set_extent([270,350,15,65],crs=ccrs.PlateCarree())
    ax.add_geometries([subp], crs=ccrs.PlateCarree(),facecolor='none',edgecolor='black', alpha=0.8, linewidth=0.75)
    ax.add_geometries([subt], crs=ccrs.PlateCarree(),facecolor='none',edgecolor='black', alpha=0.8, linewidth=0.75)
    
    ax.add_feature(cfeature.GSHHSFeature(edgecolor='k',zorder=1,facecolor='lightgrey',linewidth=0.5))
    
plt.subplots_adjust(wspace=0.15, hspace=0.1)

#ax.text(-0.07, 0.55, 'Multi-data Mean', va='bottom', ha='center',
#        rotation='vertical', rotation_mode='anchor',
#        transform=ax.transAxes, fontsize=10)

fig.subplots_adjust(left=0.2)
cbar_ax = fig.add_axes([0.15, 0.175, 0.02, 0.65])
tick = np.linspace(-3e-4, 3e-4, 7, endpoint=True)
cbar = fig.colorbar(p, cax=cbar_ax, extendrect = True,
             ticks=tick, ticklocation='left',format='%.0e').set_label(label='Mean CO$_2$ Flux \n Pg C$\cdot$year$^{-1}$',size=10,weight='semibold')
#cbar.formatter.set_powerlimits((0, 0))
#cbar.ax.set_xticklabels(['-3x10^$-4$', '-2x10^$-4$', '-1x10^$-4$','0','1x10^$-4$','2x10^$-4$','3x10^$-4$'])  # horizontal colorbar

plt.savefig('2022_Fig1Panela.png')

In [14]:
fig, axs = plt.subplots(1, 5, figsize=(18,2.5), dpi=600)

ax1          =plt.subplot(1,5,1)
    
for i in range(0,6):
    sns.kdeplot(co2_ym[i],fill=True, color='red', common_norm=False,
    alpha=.1, linewidth=0)
    
    sns.kdeplot(co2_ym[6], color='red')
    sns.kdeplot(co2_ym[7], color='black')

ax1.set_title('k', fontsize=10, loc='left', fontweight='semibold')

ax1.set_ylim(0,20)
ax1.set_xlim(-1,0)
ax1.axvspan(-1, 0, facecolor='dodgerblue', alpha=0.1)

ax1.set_yticks([0,10,20], fontsize=10)
ax1.set_xticks([-1,-0.5,0], fontsize=10)


ax2          =plt.subplot(1,5,2)
    
for i in range(0,6):
    sns.kdeplot(co2_win[i],fill=True, color='red', common_norm=False,
    alpha=.1, linewidth=0,)
    
    sns.kdeplot(co2_win[6], color='red')
    sns.kdeplot(co2_win[7], color='black')

ax2.set_title('l', fontsize=10, loc='left', fontweight='semibold')

ax2.set_yticks([0,10,20], fontsize=10)
ax2.set_xticks([-1,-0.5,0], fontsize=10)

ax2.set_ylim(0,20)
ax2.set_xlim(-1,0)
ax2.axvspan(0, -1, facecolor='dodgerblue', alpha=0.1)
plt.ylabel('')

ax3          =plt.subplot(1,5,3)
    
for i in range(0,6):
    sns.kdeplot(co2_spr[i],fill=True, color='red', common_norm=False, 
    alpha=.1, linewidth=0,)
    
    sns.kdeplot(co2_spr[6], color='red')
    sns.kdeplot(co2_spr[7], color='black')

ax3.set_title('m', fontsize=10, loc='left', fontweight='semibold')

plt.yticks([0,10,20], fontsize=10)
plt.xticks([-1,-0.5,0], fontsize=10)

ax3.set_ylim(0,20)
ax3.set_xlim(-1,0)
ax3.axvspan(0, -1, facecolor='dodgerblue', alpha=0.1)

plt.ylabel('')

ax4          =plt.subplot(1,5,4)
    
for i in range(0,6):
    sns.kdeplot(co2_sum[i],fill=True, color='red', common_norm=False, 
    alpha=.1, linewidth=0,)
    
    sns.kdeplot(co2_sum[6], color='red')
    sns.kdeplot(co2_sum[7], color='black')
    

ax4.set_title('n', fontsize=10, loc='left', fontweight='semibold')

plt.yticks([0,10,20], fontsize=10)
plt.xticks([-0.5,0,0.5], fontsize=10)

ax4.set_ylim(0,20)
ax4.set_xlim(-0.5,0.5)

ax4.axvspan(0, -0.5, facecolor='dodgerblue', alpha=0.1)
ax4.axvspan(0, 0.5, facecolor='orange', alpha=0.1)

plt.ylabel('')

ax5          =plt.subplot(1,5,5)
    
for i in range(0,6):
    sns.kdeplot(co2_aut[i],fill=True, color='red', common_norm=False,
    alpha=.1, linewidth=0,)
    
    sns.kdeplot(co2_aut[6], color='red', label='Multi-data Mean')
    sns.kdeplot(co2_aut[7], color='black',label='MPI-GE Mean')
    

ax5.set_title('o', fontsize=10, loc='left', fontweight='semibold')

plt.ylabel("")

plt.yticks([0,30,60], fontsize=10)
plt.xticks([-0.75,-0.25,0.25], fontsize=10)

ax5.set_ylim(0,60)
ax5.set_xlim(-0.75,0.25)
ax5.axvspan(0, -0.75, facecolor='dodgerblue', alpha=0.1)
ax5.axvspan(0, 0.25, facecolor='orange', alpha=0.1)

plt.savefig('2022_Fig1Panelb.png')

### Uncertainty estimates

In [ ]:
mpige_co2_members_ym=[]
mpige_co2_members_win=[]
mpige_co2_members_spr=[]
mpige_co2_members_sum=[]
mpige_co2_members_aut=[]


for i in range(1,101):    
    print(i, end='\r')
    f='{}{}{}'.format('../data/GE_co2_',i,'.nc')
    
    a1=cdo.sellonlatbox('-89,-10,15,65', input=f, options='-f nc')
    a =cdo.setclonlatbox('0,-89,-60,50,65',input=a1, options='-f nc')
    
    b=cdo.yearmean(input=a, options='-f nc')
    c=cdo.timmean(input=b, options='-f nc')
    
    d=Dataset(c, 'r')
    mpige_co2_members_ym.append(np.round(np.nansum(d.variables['co2flux'][:,0,:,:]),decimals=3))
    
    e=cdo.select('season=DJF', input=a, options='-f nc')
    f=cdo.yearmean(input=e, options='-f nc')
    g=cdo.timmean(input=f, options='-f nc')
    
    h=Dataset(g, 'r')
    mpige_co2_members_win.append(np.round(np.nansum(h.variables['co2flux'][:,0,:,:]),decimals=3))
    
    i=cdo.select('season=MAM', input=a, options='-f nc')
    j=cdo.yearmean(input=i, options='-f nc')
    k=cdo.timmean(input=j, options='-f nc')
    
    l=Dataset(k, 'r')
    mpige_co2_members_spr.append(np.round(np.nansum(l.variables['co2flux'][:,0,:,:]),decimals=3))
    
    m=cdo.select('season=JJA', input=a, options='-f nc')
    n=cdo.yearmean(input=m, options='-f nc')
    o=cdo.timmean(input=n, options='-f nc')
    
    p=Dataset(o, 'r')
    mpige_co2_members_sum.append(np.round(np.nansum(p.variables['co2flux'][:,0,:,:]),decimals=3))
    
    q=cdo.select('season=SON', input=a, options='-f nc')
    r=cdo.yearmean(input=q, options='-f nc')
    s=cdo.timmean(input=r, options='-f nc')
    
    t=Dataset(s, 'r')
    mpige_co2_members_aut.append(np.round(np.nansum(t.variables['co2flux'][:,0,:,:]),decimals=3))

In [81]:
# # Uncertainty range for model ensemble
mod_uncertainty = ((np.max(mpige_co2_members_ym)-np.min(mpige_co2_members_ym))/2,
                  (np.max(mpige_co2_members_win)-np.min(mpige_co2_members_win))/2,
                  (np.max(mpige_co2_members_spr)-np.min(mpige_co2_members_spr))/2,
                  (np.max(mpige_co2_members_sum)-np.min(mpige_co2_members_sum))/2,
                  (np.max(mpige_co2_members_aut)-np.min(mpige_co2_members_aut))/2)
mod_uncertainty = np.round(mod_uncertainty,2)

# Mean values ± Range
print(str(np.round(np.mean(mpige_co2_members_ym[:]),decimals=2)) +u" \u00B1 "+ str(mod_uncertainty[0]) + 'Pg C/yr')
print(str((np.mean(mpige_co2_members_win[:])/4).round(2)) +u" \u00B1 " + str(mod_uncertainty[1]) +'Pg C/yr')
print(str((np.mean(mpige_co2_members_spr[:])/4).round(2)) +u" \u00B1 " + str(mod_uncertainty[2]) +'Pg C/yr')
print(str((np.mean(mpige_co2_members_sum[:])/4).round(2)) +u" \u00B1 " + str(mod_uncertainty[3]) +'Pg C/yr')
print(str((np.mean(mpige_co2_members_aut[:])/4).round(2)) +u" \u00B1 " + str(mod_uncertainty[4]) +'Pg C/yr')

-0.31 ± 0.02Pg C/yr
-0.16 ± 0.03Pg C/yr
-0.19 ± 0.02Pg C/yr
0.03 ± 0.02Pg C/yr
0.02 ± 0.02Pg C/yr


In [ ]:
# Uncertainty range for obs-based products

obs_uncertainty = ((np.max(co2_ym)-np.min(co2_ym))/2,
                  (np.max(co2_win)-np.min(co2_win))/2,
                  (np.max(co2_spr)-np.min(co2_spr))/2,
                  (np.max(co2_sum)-np.min(co2_sum))/2,
                  (np.max(co2_aut)-np.min(co2_aut))/2)
obs_uncertainty = np.round(obs_uncertainty,2)

# Mean values ± Range
print(str(np.round(np.mean(co2_ym[:]),decimals=2)) +u" \u00B1 "+ str(obs_uncertainty[0]) + 'Pg C/yr')
print(str((np.mean(co2_win[:])/4).round(2)) +u" \u00B1 " + str(obs_uncertainty[1]) +'Pg C/yr')
print(str((np.mean(co2_spr[:])/4).round(2)) +u" \u00B1 " + str(obs_uncertainty[2]) +'Pg C/yr')
print(str((np.mean(co2_sum[:])/4).round(2)) +u" \u00B1 " + str(obs_uncertainty[3]) +'Pg C/yr')
print(str((np.mean(co2_aut[:])/4).round(2)) +u" \u00B1 " + str(obs_uncertainty[4]) +'Pg C/yr')

-0.33 ± 0.18Pg C/yr
-0.13 ± 0.28Pg C/yr
-0.13 ± 0.29Pg C/yr
-0.02 ± 0.19Pg C/yr
-0.04 ± 0.23Pg C/yr
